### Challenge for Extra Credit (3 pts in overall grade)

1. Add obstacles
  - Use something like this to define the obstacles (start and goal position are also defined)
```python
# Define environment
start_position = (1, 1)
goal = (9, 9)
obstacles = [(3, 3, 2, 2), (6, 6, 2, 2), (2, 7, 2, 1)]  # (x, y, width, height)
```
  - Need additional logic to check if the path has collisions with the obstacles
2. Implement RRT*
3. Show in animation the progress of the pathfinding process of RRT* in an environment with obstacles
  - Animation means when the code is running, the graph shows every new node added to the tree step by step, instead of the graph shows all the nodes added at the end of the process.

In [83]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

class Tree:
    def __init__(self, start):
        self.nodes = [start]
        self.edges = []

    def add_node(self, new_point, parent_point):
        self.nodes.append(new_point)
        self.edges.append((parent_point, new_point))

    def nearest_node(self, point):
        return min(self.nodes, key=lambda n: np.linalg.norm(np.array(n) - np.array(point)))

def generate_random_point(bounds):
    return (np.random.uniform(bounds[0], bounds[1]), np.random.uniform(bounds[2], bounds[3]))

def collides_with_obstacle(point, obstacles):
    x, y = point
    for ox, oy, w, h in obstacles:
        if ox <= x <= ox + w and oy <= y <= oy + h:
            return True
    return False

def line_intersects_rect(p1, p2, rect):
    ox, oy, w, h = rect
    x1, y1 = p1
    x2, y2 = p2

    rect_edges = [
        ((ox, oy), (ox + w, oy)),
        ((ox, oy), (ox, oy + h)),
        ((ox + w, oy), (ox + w, oy + h)),
        ((ox, oy + h), (ox + w, oy + h))
    ]

    def ccw(A, B, C):
        return (C[1] - A[1]) * (B[0] - A[0]) > (B[1] - A[1]) * (C[0] - A[0])

    def lines_intersect(A, B, C, D):
        return ccw(A, C, D) != ccw(B, C, D) and ccw(A, B, C) != ccw(A, B, D)

    for edge in rect_edges:
        if lines_intersect(p1, p2, edge[0], edge[1]):
            return True
    return False

def grow_tree_step(tree, bounds, obstacles, radius=1.5, step_size=1.0):
    new_point = generate_random_point(bounds)
    if not collides_with_obstacle(new_point, obstacles):
        nearest_node = tree.nearest_node(new_point)

        direction = np.array(new_point) - np.array(nearest_node)
        distance = np.linalg.norm(direction)
        if distance > step_size:
            direction = (direction / distance) * step_size
            new_point = tuple(np.array(nearest_node) + direction)

        if any(line_intersects_rect(nearest_node, new_point, rect) for rect in obstacles):
            return tree

        tree.add_node(new_point, nearest_node)

        for node in tree.nodes:
            if np.linalg.norm(np.array(node) - np.array(new_point)) < radius and node != nearest_node:
                if (nearest_node, new_point) in tree.edges:
                    tree.edges.remove((nearest_node, new_point))
                if not any(line_intersects_rect(node, new_point, rect) for rect in obstacles):
                    tree.edges.append((node, new_point))

    return tree

def update(frame, tree, bounds, obstacles, ax, nodes_plot, edges_plot):
    tree = grow_tree_step(tree, bounds, obstacles)
    edges_x, edges_y = [], []
    for edge in tree.edges:
        edges_x.extend([edge[0][0], edge[1][0], None])
        edges_y.extend([edge[0][1], edge[1][1], None])
    nodes_x, nodes_y = zip(*tree.nodes)
    edges_plot.set_data(edges_x, edges_y)
    nodes_plot.set_offsets(np.c_[nodes_x, nodes_y])
    return edges_plot, nodes_plot

def animate_tree(tree, bounds, obstacles, frames=100):
    fig, ax = plt.subplots(figsize=(6,6))
    for ox, oy, w, h in obstacles:
        ax.add_patch(plt.Rectangle((ox, oy), w, h, color='gray'))
    ax.set_xlim(bounds[0], bounds[1])
    ax.set_ylim(bounds[2], bounds[3])
    ax.set_title("RRT* Pathfinding with Obstacles")
    nodes_plot = ax.scatter([], [], c='red', marker='o')
    edges_plot, = ax.plot([], [], 'b-')
    anim = FuncAnimation(fig, update, frames=frames, fargs=(tree, bounds, obstacles, ax, nodes_plot, edges_plot), blit=True, repeat=False)
    return HTML(anim.to_jshtml())

start_position = (1, 1)
goal = (9, 9)
obstacles = [(3, 3, 2, 2), (6, 6, 2, 2), (2, 7, 2, 1)]
rrt_star_tree = Tree(start_position)
display(animate_tree(rrt_star_tree, (0, 10, 0, 10), obstacles))
